In [4]:
%load_ext autoreload
%autoreload 2
%reload_ext autoreload

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [5]:
import MDAnalysis as mda
from MDAnalysis.analysis import align

import nglview as nv
import ipywidgets as widgets

import matplotlib.pyplot as plt
import matplotlib.colors
import matplotlib.cm as cm
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go

import numpy as np
import pandas as pd

import conserved_atoms.main as ca


In [6]:
stride = 5

In [7]:
# u = mda.Universe('run.pdb', 'run_100ps.xtc')
u = mda.Universe('show.gro', 'compact-skip100.xtc')

In [8]:
binding_pocket = u.select_atoms('(cyzone 12 20 -20 protein) and protein')

view = nv.show_mdanalysis(binding_pocket)
# view.add_licorice()

bp_center = binding_pocket.centroid()
view.shape.add_sphere(bp_center, # Location
                      matplotlib.colors.to_rgba('#A43820', alpha=.6),
                      0.6, # Radius 
                      f"Binding pocket centroid") # Label

view

NGLWidget(max_frame=500)

In [9]:
df = ca.calc_density(u, pocket_definition='cyzone 12 20 -20 protein', target='OW', align_on='CA')

Aligning trajectory on cyzone 12 20 -20 protein and name CA.
(Note: You might have to realign if you want to calculate other variables that depend on relative distances.)
Aligning...done
Extracting atoms...done
Calculating denstity...done


In [10]:
df

x          y          z     id name   time   density
0      48.870003  46.330002  55.480003  37436   OW    0.0  0.000021
1      42.340004  35.100002  33.390003  38453   OW    0.0  0.000119
2      56.370003  47.970005  68.960007  38903   OW    0.0  0.000272
3      55.610004  37.810001  64.750000  39926   OW    0.0  0.000189
4      50.530006  41.380001  52.160000  40049   OW    0.0  0.000238
...          ...        ...        ...    ...  ...    ...       ...
55974  44.002483  45.597271  40.987476  93539   OW  100.0  0.000194
55975  42.193336  35.217014  35.200092  93785   OW  100.0  0.000152
55976  51.014488  44.822914  34.920670  94160   OW  100.0  0.000150
55977  42.984188  44.861629  48.389668  94409   OW  100.0  0.000215
55978  56.715191  48.774521  59.725002  94697   OW  100.0  0.000222

[55979 rows x 7 columns]

In [11]:
fig = px.scatter_3d(df[df.index % stride == 0],
                    x='x',
                    y='y',
                    z='z',
                    symbol='name',
                    color='density',
                    color_continuous_scale='Spectral_r')

fig.update_traces(marker=dict(size=2,
                              line=dict(width=2,
                                        color='DarkSlateGrey')),
                  selector=dict(mode='markers'))

fig.update_scenes(aspectmode='data')


In [12]:
df_clustered, df_summary = ca.cluster(df, u.trajectory.n_frames)
# df_clustered, df_summary = ca.cluster(df, u.trajectory.n_frames, density_cutoff=0.00006)

In [21]:
fig = go.Figure(go.Scatter3d(
        x=df_clustered[df_clustered['cluster_id'] != -1]['x'],
        y=df_clustered[df_clustered['cluster_id'] != -1]['y'],
        z=df_clustered[df_clustered['cluster_id'] != -1]['z'],
        mode='markers',
        marker = dict(
            size=2,
            line=dict(width=2,
                    color='DarkSlateGrey'),
            color=df_clustered[df_clustered['cluster_id'] != -1]['cluster_id'],
            colorscale='spectral',
            opacity=1
        )
    ))

fig.show()

In [26]:
df_vox = ca.voxelize(df_clustered)

Voxelizing...done
Reduced number of points from 55979 to 4180 points. (93% reduction)


In [27]:
df_vox

x          y          z       id       time   density  \
0     39.294598  39.906884  38.891277  51044.0  15.000000  0.000161   
1     39.294598  40.601652  38.891277  62122.5  43.233333  0.000191   
2     39.294598  40.601652  40.105261  56555.0  71.400000  0.000186   
3     39.294598  41.296421  40.105261  90146.0  99.600000  0.000196   
4     39.294598  41.296421  42.533228  47306.0  27.400000  0.000108   
...         ...        ...        ...      ...        ...       ...   
4175  62.505571  38.517347  49.817130  92984.0  35.300000  0.000073   
4176  62.505571  39.212116  48.603146  80619.5  64.883333  0.000070   
4177  62.505571  39.212116  49.817130  92984.0  75.100000  0.000076   
4178  62.505571  39.906884  48.603146  88065.5  79.300000  0.000058   
4179  62.505571  46.159800  63.170950  56315.0  80.600000  0.000089   

      cluster_id  mahalanobis         p  occupancy  
0           36.0     1.489855  0.474769   0.255489  
1           36.0     1.511365  0.496326   0.255489  
2           36.0     0.364292  0.833479   0.255489  
3           36.0     2.477681  0.289720   0.255489  
4           28.0     1.846499  0.397226   0.357285  
...          ...          ...       ...        ...  
4175        26.0     1.920208  0.420244   0.351297  
4176        26.0     1.366876  0.521979   0.351297  
4177        26.0     1.807539  0.426332   0.351297  
4178        26.0     2.226413  0.334351   0.351297  
4179         1.0     0.913384  0.633375   1.556886  

[4180 rows x 10 columns]

In [29]:
fig = go.Figure(go.Scatter3d(
        x=df_vox['x'],
        y=df_vox['y'],
        z=df_vox['z'],
        mode='markers',
        marker = dict(
            size=2,
            line=dict(width=2,
                    color='DarkSlateGrey'),
            color=df_vox['density'],
            colorscale='spectral_r',
            opacity=1
        )
    ))

fig.show()